In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader
from torchvision.datasets import ImageFolder
import torchvision.transforms as T
from torchvision.utils import save_image
import os
from tqdm.notebook import tqdm
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
DATA_DIR = r'C:\Users\Keerthivasan\Desktop\Machine Learning\archive\chest_xray\train'
image_size = 256
batch_size = 8

transform = T.Compose([
    T.Resize(image_size),
    T.CenterCrop(image_size),
    T.ToTensor(),
    T.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))
])

train_ds = ImageFolder(DATA_DIR, transform=transform)
train_dl = DataLoader(train_ds, batch_size=batch_size, shuffle=True, num_workers=3, pin_memory=True)
latent_size = 256

class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()

        self.init_size = image_size // 4
        self.l1 = nn.Sequential(nn.Linear(latent_size, 128 * self.init_size ** 2))

        self.conv_blocks = nn.Sequential(
            nn.BatchNorm2d(128),
            nn.Upsample(scale_factor=2),
            nn.Conv2d(128, 128, 3, stride=1, padding=1),
            nn.BatchNorm2d(128, 0.8),
            nn.LeakyReLU(0.2, inplace=True),
            nn.Upsample(scale_factor=2),
            nn.Conv2d(128, 64, 3, stride=1, padding=1),
            nn.BatchNorm2d(64, 0.8),
            nn.LeakyReLU(0.2, inplace=True),
            nn.Conv2d(64, 3, 3, stride=1, padding=1),
            nn.Tanh(),
        )

    def forward(self, z):
        out = self.l1(z)
        out = out.view(out.shape[0], 128, self.init_size, self.init_size)
        img = self.conv_blocks(out)
        return img

class Discriminator(nn.Module):
    def __init__(self):
        super(Discriminator, self).__init__()

        def discriminator_block(in_filters, out_filters, bn=True):
            block = [nn.Conv2d(in_filters, out_filters, 3, 2, 1), nn.LeakyReLU(0.2, inplace=True), nn.Dropout2d(0.25)]
            if bn:
                block.append(nn.BatchNorm2d(out_filters, 0.8))
            return block

        self.model = nn.Sequential(
            *discriminator_block(3, 16, bn=False),
            *discriminator_block(16, 32),
            *discriminator_block(32, 64),
            *discriminator_block(64, 128),
        )
        ds_size = image_size // 2 ** 4
        self.adv_layer = nn.Linear(128 * ds_size ** 2, 1)

    def forward(self, img):
        out = self.model(img)
        out = out.view(out.shape[0], -1)
        validity = self.adv_layer(out)
        return validity
generator = Generator().to(device)
discriminator = Discriminator().to(device)
adversarial_loss = torch.nn.BCEWithLogitsLoss()
lr = 0.0002
optimizer_G = torch.optim.Adam(generator.parameters(), lr=lr, betas=(0.5, 0.999))
optimizer_D = torch.optim.Adam(discriminator.parameters(), lr=lr, betas=(0.5, 0.999))
num_epochs = 100
sample_interval = 200

for epoch in range(num_epochs):
    for i, (imgs, _) in enumerate(train_dl):
        batch_size = imgs.size(0)
        valid = torch.FloatTensor(batch_size, 1).fill_(1.0).to(device)
        fake = torch.FloatTensor(batch_size, 1).fill_(0.0).to(device)
        real_imgs = imgs.to(device)
        optimizer_G.zero_grad()
        z = torch.randn(batch_size, latent_size).to(device)
        gen_imgs = generator(z)
        g_loss = adversarial_loss(discriminator(gen_imgs), valid)

        g_loss.backward()
        optimizer_G.step()
        optimizer_D.zero_grad()
        real_loss = adversarial_loss(discriminator(real_imgs), valid[:batch_size])  
        fake_loss = adversarial_loss(discriminator(gen_imgs.detach()), fake[:batch_size])  
        d_loss = (real_loss + fake_loss) / 2

        d_loss.backward()
        optimizer_D.step()
        print(
            "[Epoch %d/%d] [Batch %d/%d] [D loss: %f] [G loss: %f]"
            % (epoch, num_epochs, i, len(train_dl), d_loss.item(), g_loss.item())
        )

        batches_done = epoch * len(train_dl) + i
        if batches_done % sample_interval == 0:
            os.makedirs('images', exist_ok=True)
            save_image(gen_imgs.data[:25], "images/%d.png" % batches_done, nrow=5, normalize=True)

[Epoch 0/100] [Batch 0/654] [D loss: 0.691195] [G loss: 0.695615]
[Epoch 0/100] [Batch 1/654] [D loss: 0.687183] [G loss: 0.695123]
[Epoch 0/100] [Batch 2/654] [D loss: 0.680238] [G loss: 0.695652]
[Epoch 0/100] [Batch 3/654] [D loss: 0.665867] [G loss: 0.696117]
[Epoch 0/100] [Batch 4/654] [D loss: 0.650577] [G loss: 0.695493]
[Epoch 0/100] [Batch 5/654] [D loss: 0.638025] [G loss: 0.697277]
[Epoch 0/100] [Batch 6/654] [D loss: 0.612412] [G loss: 0.697816]
[Epoch 0/100] [Batch 7/654] [D loss: 0.604392] [G loss: 0.697695]
[Epoch 0/100] [Batch 8/654] [D loss: 0.574349] [G loss: 0.698660]
[Epoch 0/100] [Batch 9/654] [D loss: 0.555169] [G loss: 0.701324]
[Epoch 0/100] [Batch 10/654] [D loss: 0.464188] [G loss: 0.700451]
[Epoch 0/100] [Batch 11/654] [D loss: 0.417273] [G loss: 0.700633]
[Epoch 0/100] [Batch 12/654] [D loss: 0.420064] [G loss: 0.723464]
[Epoch 0/100] [Batch 13/654] [D loss: 0.399676] [G loss: 0.690711]
[Epoch 0/100] [Batch 14/654] [D loss: 0.368763] [G loss: 0.703702]
[Epoc

[Epoch 0/100] [Batch 124/654] [D loss: 0.655938] [G loss: 0.840351]
[Epoch 0/100] [Batch 125/654] [D loss: 0.629854] [G loss: 0.727522]
[Epoch 0/100] [Batch 126/654] [D loss: 0.762401] [G loss: 0.807168]
[Epoch 0/100] [Batch 127/654] [D loss: 0.709078] [G loss: 0.772311]
[Epoch 0/100] [Batch 128/654] [D loss: 0.729828] [G loss: 0.664567]
[Epoch 0/100] [Batch 129/654] [D loss: 0.592639] [G loss: 0.824364]
[Epoch 0/100] [Batch 130/654] [D loss: 0.630227] [G loss: 0.848969]
[Epoch 0/100] [Batch 131/654] [D loss: 0.617113] [G loss: 0.671441]
[Epoch 0/100] [Batch 132/654] [D loss: 0.590866] [G loss: 0.990680]
[Epoch 0/100] [Batch 133/654] [D loss: 0.689827] [G loss: 0.812618]
[Epoch 0/100] [Batch 134/654] [D loss: 0.585183] [G loss: 0.706167]
[Epoch 0/100] [Batch 135/654] [D loss: 0.698296] [G loss: 0.806953]
[Epoch 0/100] [Batch 136/654] [D loss: 0.673907] [G loss: 0.660446]
[Epoch 0/100] [Batch 137/654] [D loss: 0.625440] [G loss: 0.749859]
[Epoch 0/100] [Batch 138/654] [D loss: 0.664645]

[Epoch 0/100] [Batch 245/654] [D loss: 0.681656] [G loss: 0.637284]
[Epoch 0/100] [Batch 246/654] [D loss: 0.758670] [G loss: 0.704867]
[Epoch 0/100] [Batch 247/654] [D loss: 0.698299] [G loss: 0.752822]
[Epoch 0/100] [Batch 248/654] [D loss: 0.693232] [G loss: 0.633727]
[Epoch 0/100] [Batch 249/654] [D loss: 0.660977] [G loss: 0.735076]
[Epoch 0/100] [Batch 250/654] [D loss: 0.641085] [G loss: 0.711436]
[Epoch 0/100] [Batch 251/654] [D loss: 0.702997] [G loss: 0.736281]
[Epoch 0/100] [Batch 252/654] [D loss: 0.720613] [G loss: 0.587283]
[Epoch 0/100] [Batch 253/654] [D loss: 0.633758] [G loss: 0.757927]
[Epoch 0/100] [Batch 254/654] [D loss: 0.634443] [G loss: 0.674693]
[Epoch 0/100] [Batch 255/654] [D loss: 0.688027] [G loss: 0.888389]
[Epoch 0/100] [Batch 256/654] [D loss: 0.760685] [G loss: 0.763930]
[Epoch 0/100] [Batch 257/654] [D loss: 0.635855] [G loss: 0.816800]
[Epoch 0/100] [Batch 258/654] [D loss: 0.708617] [G loss: 0.754787]
[Epoch 0/100] [Batch 259/654] [D loss: 0.730574]

[Epoch 0/100] [Batch 367/654] [D loss: 0.587504] [G loss: 1.053280]
[Epoch 0/100] [Batch 368/654] [D loss: 0.640382] [G loss: 0.867293]
[Epoch 0/100] [Batch 369/654] [D loss: 0.658329] [G loss: 0.910687]
[Epoch 0/100] [Batch 370/654] [D loss: 0.682699] [G loss: 0.606499]
[Epoch 0/100] [Batch 371/654] [D loss: 0.608995] [G loss: 0.725276]
[Epoch 0/100] [Batch 372/654] [D loss: 0.640762] [G loss: 0.720634]
[Epoch 0/100] [Batch 373/654] [D loss: 0.640315] [G loss: 0.707648]
[Epoch 0/100] [Batch 374/654] [D loss: 0.720939] [G loss: 0.774601]
[Epoch 0/100] [Batch 375/654] [D loss: 0.736719] [G loss: 0.658579]
[Epoch 0/100] [Batch 376/654] [D loss: 0.671692] [G loss: 0.944084]
[Epoch 0/100] [Batch 377/654] [D loss: 0.705614] [G loss: 0.852937]
[Epoch 0/100] [Batch 378/654] [D loss: 0.695430] [G loss: 0.673695]
[Epoch 0/100] [Batch 379/654] [D loss: 0.692982] [G loss: 0.742764]
[Epoch 0/100] [Batch 380/654] [D loss: 0.648892] [G loss: 0.700062]
[Epoch 0/100] [Batch 381/654] [D loss: 0.642358]

[Epoch 0/100] [Batch 489/654] [D loss: 0.536790] [G loss: 0.937437]
[Epoch 0/100] [Batch 490/654] [D loss: 0.542787] [G loss: 1.010354]
[Epoch 0/100] [Batch 491/654] [D loss: 0.568554] [G loss: 0.966240]
[Epoch 0/100] [Batch 492/654] [D loss: 0.591992] [G loss: 1.175673]
[Epoch 0/100] [Batch 493/654] [D loss: 0.765719] [G loss: 0.896247]
[Epoch 0/100] [Batch 494/654] [D loss: 0.557775] [G loss: 0.851250]
[Epoch 0/100] [Batch 495/654] [D loss: 0.736739] [G loss: 0.428891]
[Epoch 0/100] [Batch 496/654] [D loss: 0.635213] [G loss: 0.634129]
[Epoch 0/100] [Batch 497/654] [D loss: 0.786719] [G loss: 0.723231]
[Epoch 0/100] [Batch 498/654] [D loss: 0.680884] [G loss: 0.587850]
[Epoch 0/100] [Batch 499/654] [D loss: 0.708681] [G loss: 0.768967]
[Epoch 0/100] [Batch 500/654] [D loss: 0.623690] [G loss: 0.937091]
[Epoch 0/100] [Batch 501/654] [D loss: 0.513020] [G loss: 0.934162]
[Epoch 0/100] [Batch 502/654] [D loss: 0.576733] [G loss: 0.660641]
[Epoch 0/100] [Batch 503/654] [D loss: 0.612936]

...

[Epoch 90/100] [Batch 7/654] [D loss: 0.333968] [G loss: 2.192401]
[Epoch 90/100] [Batch 8/654] [D loss: 0.488500] [G loss: 1.126475]
[Epoch 90/100] [Batch 9/654] [D loss: 0.215745] [G loss: 1.796088]
[Epoch 90/100] [Batch 10/654] [D loss: 0.323373] [G loss: 1.275183]
[Epoch 90/100] [Batch 11/654] [D loss: 0.387229] [G loss: 2.659104]
[Epoch 90/100] [Batch 12/654] [D loss: 0.726343] [G loss: 1.025304]
[Epoch 90/100] [Batch 13/654] [D loss: 0.297406] [G loss: 2.009281]
[Epoch 90/100] [Batch 14/654] [D loss: 0.522944] [G loss: 2.091945]
[Epoch 90/100] [Batch 15/654] [D loss: 0.483716] [G loss: 0.772505]
[Epoch 90/100] [Batch 16/654] [D loss: 0.347943] [G loss: 0.960786]
[Epoch 90/100] [Batch 17/654] [D loss: 0.381225] [G loss: 0.633494]
[Epoch 90/100] [Batch 18/654] [D loss: 0.262085] [G loss: 1.662976]
[Epoch 90/100] [Batch 19/654] [D loss: 0.611439] [G loss: 1.080916]
[Epoch 90/100] [Batch 20/654] [D loss: 0.396861] [G loss: 2.119926]
[Epoch 90/100] [Batch 21/654] [D loss: 0.324992] [G

[Epoch 90/100] [Batch 128/654] [D loss: 0.465652] [G loss: 2.023359]
[Epoch 90/100] [Batch 129/654] [D loss: 0.591701] [G loss: 1.784109]
[Epoch 90/100] [Batch 130/654] [D loss: 0.246675] [G loss: 1.657053]
[Epoch 90/100] [Batch 131/654] [D loss: 0.531854] [G loss: 1.921458]
[Epoch 90/100] [Batch 132/654] [D loss: 0.430765] [G loss: 1.256773]
[Epoch 90/100] [Batch 133/654] [D loss: 1.295531] [G loss: 0.794505]
[Epoch 90/100] [Batch 134/654] [D loss: 0.410958] [G loss: 2.225227]
[Epoch 90/100] [Batch 135/654] [D loss: 0.451482] [G loss: 1.994489]
[Epoch 90/100] [Batch 136/654] [D loss: 0.341960] [G loss: 1.020240]
[Epoch 90/100] [Batch 137/654] [D loss: 0.524414] [G loss: 1.216404]
[Epoch 90/100] [Batch 138/654] [D loss: 0.866858] [G loss: 1.332118]
[Epoch 90/100] [Batch 139/654] [D loss: 0.529337] [G loss: 1.872368]
[Epoch 90/100] [Batch 140/654] [D loss: 0.199484] [G loss: 1.039388]
[Epoch 90/100] [Batch 141/654] [D loss: 0.668884] [G loss: 2.453580]
[Epoch 90/100] [Batch 142/654] [D 

[Epoch 90/100] [Batch 247/654] [D loss: 0.534339] [G loss: 0.897610]
[Epoch 90/100] [Batch 248/654] [D loss: 0.395562] [G loss: 1.082589]
[Epoch 90/100] [Batch 249/654] [D loss: 0.464736] [G loss: 1.190802]
[Epoch 90/100] [Batch 250/654] [D loss: 0.598543] [G loss: 1.659855]
[Epoch 90/100] [Batch 251/654] [D loss: 0.331388] [G loss: 2.464580]
[Epoch 90/100] [Batch 252/654] [D loss: 0.180986] [G loss: 1.318385]
[Epoch 90/100] [Batch 253/654] [D loss: 0.467209] [G loss: 1.641783]
[Epoch 90/100] [Batch 254/654] [D loss: 0.289802] [G loss: 1.287096]
[Epoch 90/100] [Batch 255/654] [D loss: 0.354185] [G loss: 1.106553]
[Epoch 90/100] [Batch 256/654] [D loss: 0.377274] [G loss: 1.561237]
[Epoch 90/100] [Batch 257/654] [D loss: 0.556364] [G loss: 1.250991]
[Epoch 90/100] [Batch 258/654] [D loss: 0.533558] [G loss: 1.936479]
[Epoch 90/100] [Batch 259/654] [D loss: 0.283051] [G loss: 2.012006]
[Epoch 90/100] [Batch 260/654] [D loss: 0.638350] [G loss: 2.613554]
[Epoch 90/100] [Batch 261/654] [D 

[Epoch 90/100] [Batch 366/654] [D loss: 0.518269] [G loss: 1.513140]
[Epoch 90/100] [Batch 367/654] [D loss: 0.532530] [G loss: 1.244350]
[Epoch 90/100] [Batch 368/654] [D loss: 0.494385] [G loss: 1.898322]
[Epoch 90/100] [Batch 369/654] [D loss: 0.243518] [G loss: 1.924456]
[Epoch 90/100] [Batch 370/654] [D loss: 0.299493] [G loss: 2.347374]
[Epoch 90/100] [Batch 371/654] [D loss: 0.322838] [G loss: 1.434231]
[Epoch 90/100] [Batch 372/654] [D loss: 0.330599] [G loss: 1.895274]
[Epoch 90/100] [Batch 373/654] [D loss: 0.838961] [G loss: 1.272083]
[Epoch 90/100] [Batch 374/654] [D loss: 0.264389] [G loss: 1.230329]
[Epoch 90/100] [Batch 375/654] [D loss: 0.479317] [G loss: 1.060907]
[Epoch 90/100] [Batch 376/654] [D loss: 0.700428] [G loss: 2.280883]
[Epoch 90/100] [Batch 377/654] [D loss: 0.390954] [G loss: 1.620171]
[Epoch 90/100] [Batch 378/654] [D loss: 0.522071] [G loss: 1.512963]
[Epoch 90/100] [Batch 379/654] [D loss: 0.275034] [G loss: 1.506849]
[Epoch 90/100] [Batch 380/654] [D 

[Epoch 90/100] [Batch 485/654] [D loss: 0.704804] [G loss: 3.596474]
[Epoch 90/100] [Batch 486/654] [D loss: 0.632147] [G loss: 0.553238]
[Epoch 90/100] [Batch 487/654] [D loss: 0.303690] [G loss: 1.938385]
[Epoch 90/100] [Batch 488/654] [D loss: 0.622138] [G loss: 1.785429]
[Epoch 90/100] [Batch 489/654] [D loss: 0.460554] [G loss: 1.946344]
[Epoch 90/100] [Batch 490/654] [D loss: 0.505738] [G loss: 2.308003]
[Epoch 90/100] [Batch 491/654] [D loss: 0.644642] [G loss: 1.130709]
[Epoch 90/100] [Batch 492/654] [D loss: 0.403184] [G loss: 1.599392]
[Epoch 90/100] [Batch 493/654] [D loss: 0.848487] [G loss: 0.840486]
[Epoch 90/100] [Batch 494/654] [D loss: 0.696778] [G loss: 1.734621]
[Epoch 90/100] [Batch 495/654] [D loss: 0.313152] [G loss: 1.726932]
[Epoch 90/100] [Batch 496/654] [D loss: 0.481110] [G loss: 2.161801]
[Epoch 90/100] [Batch 497/654] [D loss: 0.316135] [G loss: 1.767128]
[Epoch 90/100] [Batch 498/654] [D loss: 0.532877] [G loss: 1.882788]
[Epoch 90/100] [Batch 499/654] [D 

In [23]:
import os
import cv2
image_folder = r'C:\Users\Keerthivasan\Desktop\Machine Learning\images'
video_name = 'output_video.mp4'
images = [img for img in os.listdir(image_folder) if img.endswith(".png") or img.endswith(".jpg")]
images.sort(key=lambda x: int(x.split('.')[0]))
frame = cv2.imread(os.path.join(image_folder, images[0]))
height, width, layers = frame.shape
video = cv2.VideoWriter(video_name, cv2.VideoWriter_fourcc(*'mp4v'), 1, (width, height))
for image in images:
    video.write(cv2.imread(os.path.join(image_folder, image)))
video.release()
